# "Letalidade e Mortalidade dos casos de SRAG-COVID nos municípios do Brasil"
> "Dados dos casos de hospitalizações por SRAG do opendatasus"

- toc: true
- branch: master
- badges: true
- comments: false
- numbersections: true
- categories: [srag, letalidade]
- image: images/some_folder/your_image.png
- hide: false
- search_exclude: true
- metadata_key1: metadata_value1
- metadata_key2: metadata_value2

## Informações sobre os dados utilizados

### Localização
- Páginas com informações completas sobre os conjuntos de dados: [2019](https://opendatasus.saude.gov.br/dataset/bd-srag-2019), [2020](https://opendatasus.saude.gov.br/dataset/bd-srag-2020), [2021](https://opendatasus.saude.gov.br/dataset/bd-srag-2021)

### Origem e contexto

Desde 2009, com a pandemia de Influenza A(H1N1)pdm09, a Secretaria de Vigilância em Saúde (SVS), vinculada ao Ministério da Saúde, desenvolve a vigilância da Síndrome Respiratória Aguda Grave (SRAG) no Brasil. Em 2020 a vigilância da COVID-19 foi incorporada na rede de vigilância da Influenza e outros vírus respiratórios.

Atualmente, o sistema oficial para o registro dos casos e óbitos de SRAG no Brasil é o Sistema de Informação da Vigilância Epidemiológica da Gripe (SIVEP-Gripe).

Todos os bancos de dados epidemiológicos de SRAG, desde 2009 até os dias atuais (2021), são disponibilizados no portal https://opendatasus.saude.gov.br. 

### Informações adicionais

- No Guia de Vigilância Epidemiológica Emergência de Saúde Pública de Importância Nacional pela Doença pelo Coronavírus 2019 estão disponíveis informações sobre definições de casos, critérios de confirmação e encerramento dos casos, dentre outros. [link](https://portalarquivos.saude.gov.br/images/af_gvs_coronavirus_6ago20_ajustes-finais-2.pdf)

- Os dados da vigilância de SRAG no Brasil disponibilizados estão sujeitos a alterações decorrentes da investigação pelas equipes de vigilância epidemiológica que desenvolvem o serviço nas três esferas de gestão.

- Os dados são disponibilizados semanalmente, às quartas-feiras, podendo, excepcionalmente, a atualização ocorrer em outro dia.

- Dicionários de dados: [2019](https://opendatasus.saude.gov.br/dataset/e99cfd21-3d8c-4ff9-bd9c-04b8b2518739/resource/457727e2-0401-4d5e-af7b-2f3bb2a7c652/download/dicionario_de_dados_srag_hospitalizado_atual-sivepgripe-2019.pdf), [2020](https://opendatasus.saude.gov.br/dataset/ae90fa8f-3e94-467e-a33f-94adbb66edf8/resource/8f571374-c555-4ec0-8e44-00b1e8b11c25/download/dicionario-de-dados-srag-hospitalizado-27.07.2020-final.pdf), [2021](https://opendatasus.saude.gov.br/dataset/9f76e80f-a2f1-4662-9e37-71084eae23e3/resource/b3321e55-24e9-49ab-8651-29cf5c8f3179/download/dicionario-de-dados-srag-hospitalizado-27.07.2020-final.pdf)

In [1]:
#hide
# %run update_srag_database.py

In [2]:

#hide

import sqlite3 as sql
import pandas as pd
import numpy as np
from srag_functions import *
import altair as alt
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [3]:
#hide

db_name = 'srag'
db_path = f'data/opendatasus/{db_name}.db'
conn = sql.connect(db_path)
# df_srag = pd.read_sql(f'SELECT * FROM {db_name} WHERE ano >= 2020', conn)
df_srag = pd.read_sql(f'SELECT * FROM {db_name}', conn)

In [4]:
#hide

assert df_srag.shape[1]==32

### Dimensões dos dados: número de casos avaliados

In [5]:
#hide

print('> Dimensões:\n')
print(f'\t{df_srag.shape[0]} linhas\n\t{df_srag.shape[1]} colunas')
print('\n> Colunas:')
for col,col_type in df_srag.dtypes.sort_index().items():
    print('\t{:<15}\t{:<}'.format(col,str(col_type)))
    
    
max_semana_visualizacao = df_srag.SEM_PRI_ABS.max() - 4

> Dimensões:

	3209532 linhas
	32 colunas

> Colunas:
	CLASSI_FIN     	object
	CLASSI_OUT     	object
	CO_MUN_NOT     	object
	CO_MUN_RES     	object
	CO_MU_INTE     	object
	CS_ESCOL_N     	object
	CS_RACA        	object
	CS_SEXO        	object
	DT_ENTUTI      	object
	DT_EVOLUCA     	object
	DT_NASC        	object
	DT_SIN_PRI     	object
	EVOLUCAO       	object
	FATOR_RISC     	object
	MUN_INTE       	object
	MUN_NOT        	object
	MUN_RES        	object
	NU_IDADE_N     	int64
	REGIAO_INTE    	object
	REGIAO_NOT     	object
	REGIAO_RES     	object
	SATURACAO      	object
	SEM_PRI        	int64
	SEM_PRI_ABS    	int64
	SUPORT_VEN     	object
	UF_INTE        	object
	UF_NOT         	object
	UF_RES         	object
	UTI            	object
	ano            	int64
	faixa_etaria   	object
	idade_anos     	float64


> construção do df_pop_mun

In [6]:
#hide_input
#collapse_output

print(f'{df_srag.shape[0]} casos de SRAG.')

df = df_srag.loc[df_srag.CLASSI_FIN == 'COVID-19'].copy()

df.loc[df.UF_RES == '53_Distrito Federal','CO_MUN_RES'] = '530010'

print(f'{df.shape[0]} casos de SRAG-COVID.')
df = df.loc[df.EVOLUCAO.isin(['obito', 'cura', 'obito_outras_causas'])]
print(f'{df.shape[0]} casos de SRAG-COVID concluídos.')
df = df.groupby(['CO_MUN_RES','EVOLUCAO'],as_index=False).size()
df = df.pivot(index = 'CO_MUN_RES',columns='EVOLUCAO',values='size')
# df = df[['cura','obito', 'obito_outras_causas']].fillna(0)
df_mun_dict = df.fillna(0).to_dict()
df = df.reset_index()

file_pop_mun = 'data/IBGE/Tabela_6579_populacao_residente_estimada.csv'


df_pop_mun = pd.read_csv(file_pop_mun,header=3).dropna().rename(columns={'2020':'População (2020)'})

# df_pop_mun = pd.read_(file_pop_mun,header=2)
# cols = df_pop_mun.iloc[0,:-1].to_list() + df_pop_mun.columns[0].split()[-1:]
# df_pop_mun.columns=cols
# df_pop_mun = df_pop_mun.iloc[1:-1]
df_pop_mun['cod6_mun'] = df_pop_mun['Cód.'].str[:6]
df_pop_mun['cura'] = df_pop_mun['cod6_mun'].apply(lambda x: df_mun_dict['cura'].get(x,0))
df_pop_mun['obito'] = df_pop_mun['cod6_mun'].apply(lambda x: df_mun_dict['obito'].get(x,0))
df_pop_mun['obito_outras_causas'] = df_pop_mun['cod6_mun'].apply(lambda x: df_mun_dict['obito_outras_causas'].get(x,0))
df_pop_mun['casos_concluidos'] = df_pop_mun['cura'] + df_pop_mun['obito'] + df_pop_mun['obito_outras_causas']
df_pop_mun['letalidade'] = df_pop_mun['obito'] / df_pop_mun['casos_concluidos']
# df_pop_mun['letalidade'] = df_pop_mun['obito'].apply(lambda x: 0 if x==0 else )
df_pop_mun['mortalidade'] = 100000* (df_pop_mun['obito'] / df_pop_mun['População (2020)'])

df_pop_mun = df_pop_mun.fillna(0)
casos_mun_res = df_pop_mun['casos_concluidos'].sum()
print(f'{int(casos_mun_res)} casos de SRAG-COVID concluídos com dados de município de residência.')
df_pop_mun


3209532 casos de SRAG.
2038113 casos de SRAG-COVID.
1891911 casos de SRAG-COVID concluídos.
1891628 casos de SRAG-COVID concluídos com dados de município de residência.


Cód.                   Município  População (2020) cod6_mun     cura  \
0     1100015  Alta Floresta D'Oeste (RO)           22728.0   110001     54.0   
1     1100023              Ariquemes (RO)          109523.0   110002    331.0   
2     1100031                 Cabixi (RO)            5188.0   110003      3.0   
3     1100049                 Cacoal (RO)           85893.0   110004    382.0   
4     1100056             Cerejeiras (RO)           16204.0   110005     75.0   
...       ...                         ...               ...      ...      ...   
5565  5222005             Vianópolis (GO)           13977.0   522200     75.0   
5566  5222054         Vicentinópolis (GO)            8873.0   522205     82.0   
5567  5222203               Vila Boa (GO)            6312.0   522220      8.0   
5568  5222302          Vila Propício (GO)            5882.0   522230      5.0   
5569  5300108               Brasília (DF)         3055149.0   530010  30820.0   

        obito  obito_outras_causas  casos_concluidos  letalidade  mortalidade  
0        61.0                  0.0             115.0    0.530435   268.391411  
1       525.0                  2.0             858.0    0.611888   479.351369  
2         4.0                  0.0               7.0    0.571429    77.101002  
3       227.0                  2.0             611.0    0.371522   264.282305  
4        45.0                  0.0             120.0    0.375000   277.709208  
...       ...                  ...               ...         ...          ...  
5565     39.0                  0.0             114.0    0.342105   279.029835  
5566     25.0                  0.0             107.0    0.233645   281.753635  
5567      4.0                  0.0              12.0    0.333333    63.371356  
5568      9.0                  0.0              14.0    0.642857   153.009181  
5569  10815.0                531.0           42166.0    0.256486   353.992555  

[5570 rows x 10 columns]

In [7]:
#hide_input
#collapse_output

df_pop_mun.sort_values('letalidade').tail(100)
df_let1 = df_pop_mun.loc[df_pop_mun.letalidade == 1.0]
df_let1.shape
df_let1

Cód.                        Município  População (2020) cod6_mun  \
346   1704600            Chapada de Areia (TO)            1410.0   170460   
360   1707553                      Fátima (TO)            3830.0   170755   
379   1712157                  Lavandeira (TO)            1954.0   171215   
398   1715507          Oliveira de Fátima (TO)            1118.0   171550   
420   1718659            Rio da Conceição (TO)            2171.0   171865   
472   2101350                  Bacurituba (MA)            5670.0   210135   
485   2102077                   Bom Lugar (MA)           16438.0   210207   
487   2102150              Brejo de Areia (MA)            9014.0   210215   
492   2102374            Cachoeira Grande (MA)            9478.0   210237   
644   2111722                   Satubinha (MA)           14096.0   211172   
655   2112274                  Tufilândia (MA)            5854.0   211227   
680   2200954           Aroeiras do Itaim (PI)            2551.0   220095   
691   2201572              Belém do Piauí (PI)            3587.0   220157   
711   2202133       Campo Grande do Piauí (PI)            5965.0   220213   
755   2204352                   Geminiano (PI)            5460.0   220435   
766   2205151           Jacobina do Piauí (PI)            5729.0   220515   
791   2206050            Massapê do Piauí (PI)            6449.0   220605   
819   2207777              Patos do Piauí (PI)            6406.0   220777   
879   2210938                  Sussuapara (PI)            6767.0   221093   
888   2211506                 Vera Mendes (PI)            3080.0   221150   
1174  2409209                    Passagem (RN)            3102.0   240920   
1545  2607406                   Itacuruba (PE)            4966.0   260740   
1627  2614402                     Solidão (PE)            6021.0   261440   
2424  3116407                    Claraval (MG)            4853.0   311640   
2944  3160207     Santo Antônio do Itambé (MG)            3799.0   316020   
3004  3164803  São Sebastião do Rio Preto (MG)            1492.0   316480   
3013  3165552                   Setubinha (MG)           12378.0   316555   
3123  3202256       Governador Lindenberg (ES)           12880.0   320225   
3154  3204252                  Ponto Belo (ES)            7940.0   320425   
3167  3205010                   Sooretama (ES)           30680.0   320501   
3171  3205150                  Vila Pavão (ES)            9244.0   320515   
4190  4120150              Porto Barreiro (PR)            3184.0   412015   
4267  4125902         São Pedro do Paraná (PR)            2289.0   412590   
5335  5200829                   Amaralina (GO)            3845.0   520082   

      cura  obito  obito_outras_causas  casos_concluidos  letalidade  \
346    0.0    4.0                  0.0               4.0         1.0   
360    0.0    7.0                  0.0               7.0         1.0   
379    0.0    1.0                  0.0               1.0         1.0   
398    0.0    1.0                  0.0               1.0         1.0   
420    0.0    4.0                  0.0               4.0         1.0   
472    0.0    1.0                  0.0               1.0         1.0   
485    0.0    5.0                  0.0               5.0         1.0   
487    0.0    2.0                  0.0               2.0         1.0   
492    0.0    5.0                  0.0               5.0         1.0   
644    0.0    3.0                  0.0               3.0         1.0   
655    0.0   14.0                  0.0              14.0         1.0   
680    0.0    2.0                  0.0               2.0         1.0   
691    0.0    7.0                  0.0               7.0         1.0   
711    0.0   11.0                  0.0              11.0         1.0   
755    0.0    7.0                  0.0               7.0         1.0   
766    0.0    4.0                  0.0               4.0         1.0   
791    0.0    2.0                  0.0               2.0         1.0   
819    0.0   13.0

## Letalidade por Município
[Topo](/covid/srag/letalidade/2021/12/13/municipios.html#)

> Municípios com população acima de 4.000 habitantes (2020)

In [8]:
#hide_input
#collapse_output

# df = df_pop_mun.sort_values(by='População (2020)',ascending=False).head(5000)
df = df_pop_mun.loc[df_pop_mun['População (2020)']>= 4000]
# df = df.sort_values(by='letalidade',ascending=False).reset_index(drop=True)
df = df.reset_index()

print(df.shape)

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('letalidade:Q', bin=alt.Bin(maxbins=20)),
    alt.Y('count()', stack=None),
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart


(4709, 11)


alt.Chart(...)

> Municípios com população acima de 10.000 habitantes (2020)

In [9]:
#hide_input
#collapse_output

# df = df_pop_mun.sort_values(by='População (2020)',ascending=False).head(5000)
df = df_pop_mun.loc[df_pop_mun['População (2020)']>= 10000]
# df = df.sort_values(by='letalidade',ascending=False).reset_index(drop=True)
df = df_pop_mun.reset_index()

print(df.shape)

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('letalidade:Q', title='Letalidade', axis=alt.Axis(format='%'), bin=alt.Bin(maxbins=20)),
    alt.Y('count()', title='Frequência',stack=None),
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart


(5570, 11)


alt.Chart(...)

## Mortalidade por Município
[Topo](/covid/srag/letalidade/2021/12/13/municipios.html#)

> Municípios com população acima de 10.000 habitantes (2020)

In [10]:
df = df_pop_mun.reset_index()
df = df.sort_values('mortalidade')
df1 = df.loc[df.mortalidade> 600]
# df1.tail(10)
df1

index     Cód.                   Município  População (2020) cod6_mun  \
3703   3703  3539004                Pirangi (SP)           11471.0   353900   
5344   5344  5201603                  Araçu (GO)            3486.0   520160   
3509   3509  3521150                 Ipiguá (SP)            5476.0   352115   
5526   5526  5219308  Santa Helena de Goiás (GO)           38808.0   521930   
3481   3481  3518909             Guzolândia (SP)            5307.0   351890   
3451   3451  3516101               Florínea (SP)            2653.0   351610   
5339   5339  5201207             Anhanguera (GO)            1160.0   520120   
3631   3631  3532504         Neves Paulista (SP)            8923.0   353250   
3670   3670  3535903              Paranapuã (SP)            4095.0   353590   
3548   3548  3524808                  Jales (SP)           49201.0   352480   
4715   4715  4305504                Ciríaco (RS)            4719.0   430550   
3219   3219  3303005               Miracema (RJ)           27154.0   330300   
3410   3410  3512902              Cosmorama (SP)            7298.0   351290   
3381   3381  3510005           Cândido Mota (SP)           31346.0   351000   
3426   3426  3514403                Dracena (SP)           47043.0   351440   
4896   4896  4313490          Novo Barreiro (RS)            4175.0   431349   
3098   3098  3200136           Águia Branca (ES)            9631.0   320013   
4861   4861  4312351               Montauri (RS)            1441.0   431235   
3407   3407  3512605         Coronel Macedo (SP)            4635.0   351260   
3448   3448  3515806             Flora Rica (SP)            1430.0   351580   
4809   4809  4310330                   Imbé (RS)           23271.0   431033   
3650   3650  3534005             Onda Verde (SP)            4422.0   353400   
3287   3287  3501806      Américo de Campos (SP)            5981.0   350180   
5557   5557  5221502               Turvânia (GO)            4564.0   522150   
3814   3814  3549003          São Francisco (SP)            2817.0   354900   
3755   3755  3543501               Riversul (SP)            5443.0   354350   
3938   3938  4102208                Atalaia (PR)            3881.0   410220   
3268   3268  3500204                 Adolfo (SP)            3554.0   350020   
2632   2632  3134400                Iturama (MG)           39690.0   313440   
3823   3823  3549805  São José do Rio Preto (SP)          464983.0   354980   
4838   4838  4311429       Lajeado do Bugre (RS)            2566.0   431142   
3812   3812  3548807     São Caetano do Sul (SP)          161957.0   354880   
5423   5423  5209291               Guaraíta (GO)            1951.0   520929   
3881   3881  3554904        Três Fronteiras (SP)            5832.0   355490   
4855   4855  4312138        Mato Castelhano (RS)            2542.0   431213   
3254   3254  3305406               Sapucaia (RJ)           18249.0   330540   
3465   3465  3517406                 Guaíra (SP)           41040.0   351740   
210     210  1503754           Jacareacanga (PA)            7590.0   150375   
3468   3468  3517703                  Guará (SP)           21308.0   351770   
4456   4456  4209706            Lebon Régis (SC)           12115.0   420970   
5351   5351  5202809           Avelinópolis (GO)            2409.0   520280   
3584   3584  3528205              Macedônia (SP)            3692.0   352820   
5506   5506  5217203               Piranhas (GO)           10272.0   521720   
2284   2284  3103751                Araporã (MG)            6931.0   310375   
4924   4924  4314555                 Pirapó (RS)            2254.0   431455   
3321   3321  3504800                Bálsamo (SP)            9139.0   350480   
4468   4468  4210555                 Marema (SC)            1750.0   421055   
3674   3674  3536257                 Parisi (SP)            2169.0   353625   
3599   3599  3529609              Meridiano (SP)            3824.0   352960   
3782   3782  3546108    Santa Clara d'Oeste (SP)        

In [11]:
#hide_input
#collapse_output

# df = df_pop_mun.sort_values(by='População (2020)',ascending=False).head(5000)
# df = df_pop_mun.loc[df_pop_mun['População (2020)']>= 10000]
# df = df.sort_values(by='mortalidade',ascending=False).reset_index(drop=True)
df = df_pop_mun.reset_index()

df=df.rename({'mortalidade':'mortalidade por 100.000 hab'})

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('mortalidade:Q', title='Mortalidade por 100 mil habitantes',bin=alt.Bin(maxbins=20)),
    alt.Y('count()', title='Frequência', stack=None),
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart


alt.Chart(...)

## Letalidade e mortalidade vs percentual da população rural
[Topo](/covid/srag/letalidade/2021/12/13/municipios.html#)

> Municípios com população acima de 4.000 habitantes (2020)

In [12]:
#hide

# adição da coluna com percentual de população rural (censo 2010)

file_name = 'data/IBGE/tabela761_urbano_rural_censo_2010.csv'

df = pd.read_csv(file_name,header=4)
df = df.dropna()
df.Rural = df.Rural.replace('-','0').astype(float)
# cols = df_pop_mun.iloc[0,:-1].to_list() + df_pop_mun.columns[0].split()[-1:]
# df_pop_mun.columns=cols
# df_pop_mun = df_pop_mun.iloc[1:-1]
df['cod6_mun'] = df['Cód.'].str[:6]
df['percent_rural'] = df['Rural'] / df['Total']
df = df.set_index('cod6_mun')['percent_rural']
dict_perc_rural = df.to_dict()
dict_perc_rural

df_pop_mun_2 = df_pop_mun.copy()
df_pop_mun_2['percent_rural'] = df_pop_mun_2['cod6_mun'].apply(lambda x: dict_perc_rural.get(x,np.nan))
# df_pop_mun = df_pop_mun.dropna()
# df_pop_mun.loc[df_pop_mun.percent_rural.isna()]
df_pop_mun_2 = df_pop_mun_2.dropna()

# df = df_pop_mun.dropna().iloc[:nrows,1:]
delta = 10
df_pop_mun_2['cat_rur'] = df_pop_mun_2['percent_rural'].apply(lambda x : f'{int(x *100 / delta)*delta:02d}_{((int(x *100 / delta) + 1)*delta)}' )

df_pop_mun_2


Cód.                   Município  População (2020) cod6_mun     cura  \
0     1100015  Alta Floresta D'Oeste (RO)           22728.0   110001     54.0   
1     1100023              Ariquemes (RO)          109523.0   110002    331.0   
2     1100031                 Cabixi (RO)            5188.0   110003      3.0   
3     1100049                 Cacoal (RO)           85893.0   110004    382.0   
4     1100056             Cerejeiras (RO)           16204.0   110005     75.0   
...       ...                         ...               ...      ...      ...   
5565  5222005             Vianópolis (GO)           13977.0   522200     75.0   
5566  5222054         Vicentinópolis (GO)            8873.0   522205     82.0   
5567  5222203               Vila Boa (GO)            6312.0   522220      8.0   
5568  5222302          Vila Propício (GO)            5882.0   522230      5.0   
5569  5300108               Brasília (DF)         3055149.0   530010  30820.0   

        obito  obito_outras_causas  casos_concluidos  letalidade  mortalidade  \
0        61.0                  0.0             115.0    0.530435   268.391411   
1       525.0                  2.0             858.0    0.611888   479.351369   
2         4.0                  0.0               7.0    0.571429    77.101002   
3       227.0                  2.0             611.0    0.371522   264.282305   
4        45.0                  0.0             120.0    0.375000   277.709208   
...       ...                  ...               ...         ...          ...   
5565     39.0                  0.0             114.0    0.342105   279.029835   
5566     25.0                  0.0             107.0    0.233645   281.753635   
5567      4.0                  0.0              12.0    0.333333    63.371356   
5568      9.0                  0.0              14.0    0.642857   153.009181   
5569  10815.0                531.0           42166.0    0.256486   353.992555   

      percent_rural cat_rur  
0          0.427271   40_50  
1          0.153044   10_20  
2          0.573420   50_60  
3          0.211940   20_30  
4          0.153268   10_20  
...             ...     ...  
5565       0.269206   20_30  
5566       0.142450   10_20  
5567       0.260401   20_30  
5568       0.707677   70_80  
5569       0.034220   00_10  

[5565 rows x 12 columns]

In [13]:
#hide_input
#collapse_output

df = df_pop_mun_2.loc[df_pop_mun_2['População (2020)']>= 4000].copy()
# df = df.sort_values(by='mortalidade',ascending=False).reset_index(drop=True)
# df = df.reset_index()

# df=df.rename(columns={'mortalidade':'mortalidade por 100.000 hab'})

chart = alt.Chart(df).mark_circle(size=20)
chart = chart.encode(
    alt.X('percent_rural:Q'),
    alt.Y('mortalidade:Q'),
    color='letalidade',
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)

In [14]:
#hide_input
#collapse_output

df = df_pop_mun_2.groupby('cat_rur').sum()
df['letalidade'] = df['obito'] / df['casos_concluidos']
df['mortalidade'] = 100000* (df['obito'] / df['População (2020)'])
df = df.reset_index()
df


cat_rur  População (2020)      cura     obito  obito_outras_causas  \
0   00_10       129816963.0  927310.0  469284.0               4015.0   
1   10_20        22074936.0  125254.0   61493.0                497.0   
2   20_30        15992696.0   66744.0   38455.0                355.0   
3   30_40        12364067.0   45276.0   24530.0                294.0   
4   40_50        10900421.0   30702.0   18186.0                235.0   
5   50_60         9739872.0   25021.0   15274.0                198.0   
6   60_70         6609457.0   15327.0    9188.0                122.0   
7   70_80         3239412.0    6623.0    3833.0                 49.0   
8   80_90          871331.0    1719.0     931.0                  8.0   
9  90_100           98558.0     205.0     112.0                  4.0   

   casos_concluidos  letalidade  mortalidade  percent_rural  
0         1400609.0    0.335057   361.496671      37.673592  
1          187244.0    0.328411   278.564794     124.700911  
2          105554.0    0.364316   240.453517     196.930072  
3           70100.0    0.349929   198.397501     277.608014  
4           49123.0    0.370214   166.837593     343.189446  
5           40493.0    0.377201   156.819309     370.638893  
6           24637.0    0.372935   139.012933     344.410448  
7           10505.0    0.364874   118.323943     228.529529  
8            2658.0    0.350263   106.848029      81.112294  
9             321.0    0.348910   113.638670       8.267541

#### Letalidade

In [15]:
#hide

# df.loc[df['']]

In [16]:
#hide_input
#collapse_output

x = 129816963.0 / df['População (2020)'].sum()
print(f'Percentual da população em cidades com até 10% da população em zonas rurais: {x:.1%}')


chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('cat_rur:N', title='Percentual da população rural'),
    # alt.Y('letalidade:Q', title='Letalidade',axis=alt.Axis(format='%')),
    y='População (2020)',
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )
chart

Percentual da população em cidades com até 10% da população em zonas rurais: 61.3%


alt.Chart(...)

#### Mortalidade

In [17]:
#hide_input
#collapse_output

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('cat_rur:N', title='Percentual da população rural'),
    alt.Y('mortalidade:Q', title='Mortalidade por 100 mil habitantes'),
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )
chart

alt.Chart(...)

## Letalidade e mortalidade vs Tipologia Rural-Urbano
[Topo](/covid/srag/letalidade/2021/12/13/municipios.html#)

In [18]:
#hide_input
#collapse_output

fpath = 'data/IBGE/tipologia_municipal_rural_urbano/Tipologia_municipal_rural_urbano.xlsx'
df_tipologia = pd.read_excel(fpath,sheet_name=1)
tipol_dict = df_tipologia.set_index('CD_GCMUN')['TIPO'].to_dict()

df_pop_mun['Tipologia'] = df_pop_mun['Cód.'].apply(lambda x: tipol_dict.get(int(x),'n.d.'))
df_pop_mun

sel_cols = ['cura','obito','casos_concluidos','População (2020)']
df_tipo = df_pop_mun.groupby('Tipologia')[sel_cols].sum()

df_tipo['letalidade'] = df_tipo['obito'] / df_tipo['casos_concluidos']
df_tipo['mortalidade_por_100_mil_ha'] = 100000*(df_tipo['obito'] / df_tipo['População (2020)'])

df_tipo.sort_values('mortalidade_por_100_mil_ha').style.format(
    {'cura':'{:.0f}',
    'obito':'{:.0f}',
    'casos_concluidos':'{:.0f}',
    'População (2020)':'{:.0f}',
    'letalidade':'{:.1%}',
    'mortalidade_por_100_mil_ha':'{:.1f}'}
)


In [20]:
#hide
 
df_srag_covid = df_srag.loc[df_srag.CLASSI_FIN == 'COVID-19'].copy()
print(df_srag_covid.shape)
df_srag_covid = df_srag_covid.loc[df_srag_covid.EVOLUCAO.isin(['obito', 'cura', 'obito_outras_causas'])]
print(df_srag_covid.shape)


(2038113, 32)
(1891911, 32)


In [21]:
#hide

df_srag_covid_raca = df_srag_covid.loc[~df_srag_covid.CS_RACA.isin(['ignorado','nd'])]
print(df_srag_covid_raca.CS_RACA.unique())
df_srag_covid_raca.shape

['branca' 'parda' 'preta' 'amarela' 'indigena']


(1548986, 32)

In [22]:
#hide_input

x_col = 'CS_RACA'
cat_col = ''
sel_cols = ['UF_RES']
y_title = 'Letalidade'
# x_col = 'faixa_etaria'
# cat_col = 'CS_RACA'
# sel_cols = ['UF_RES']
selection_dict = {}
selection_dict['idade_anos'] = ' < 20'  
selection_dict['CS_RACA'] = "!= ['ignorado','nd']"

# dataFrame2Chart(df_srag,x_col,cat_col,sel_cols,selection_dict,total=[0,1])

dataFrame2Chart_edit(df_srag_covid_raca,x_col,cat_col,sel_cols,selection_dict,total=True,mark_type='bar',sort_values=True,y_title=y_title)

Seleção :
selection_dict {'idade_anos': ' < 20', 'CS_RACA': "!= ['ignorado','nd']"}:
	idade_anos  < 20
	CS_RACA != ['ignorado','nd']
	-----
	Número de casos selecionados: 34960 (2.26% do total de casos disponíveis.)

	Dimensões dos dados do gráfico: (135, 8)


alt.Chart(...)

In [23]:
#hide_input

x_col = 'CS_RACA'
cat_col = ''
sel_cols = ['UF_RES']
y_title = 'Letalidade'
# x_col = 'faixa_etaria'
# cat_col = 'CS_RACA'
# sel_cols = ['UF_RES']
selection_dict = {}
# selection_dict['idade_anos'] = ' <= 20'  
selection_dict['CS_RACA'] = "!= ['ignorado','nd']"

# dataFrame2Chart(df_srag,x_col,cat_col,sel_cols,selection_dict,total=[0,1])

dataFrame2Chart_edit(df_srag_covid_raca,x_col,cat_col,sel_cols,selection_dict,total=True,mark_type='bar',sort_values=True,y_title=y_title)

Seleção :
selection_dict {'CS_RACA': "!= ['ignorado','nd']"}:
	CS_RACA != ['ignorado','nd']
	-----
	Número de casos selecionados: 1548986 (100.00% do total de casos disponíveis.)

	Dimensões dos dados do gráfico: (146, 8)


alt.Chart(...)

## Por tamanho da população

In [24]:
#hide_input
#collapse_output

def cat_pop(pop:float):
    if pop <= 5000:
        cat = '0. até 5 mil'
    elif pop <= 10000:
        cat = '1. 5 a 10 mil'
    elif pop <=20000:
        cat = '2. 10 a 20 mil'
    elif pop <= 50000:
        cat = '3. 20 a 50 mil'
    elif pop <= 200000:
        cat = '4. 50 a 200 mil'
    elif pop <= 500000:
        cat = '5. 200 a 500 mil'
    elif pop <= 1000000:
        cat = '6. 500 mil a 1MM'
    else: #pop >= 1e6:
        cat = '7. > 1MM'
    
    return cat

# nrows = 6000
df_pop = df_pop_mun_2.dropna().iloc[:,1:]
# delta = 10
df_pop['cat_pop'] = df_pop['População (2020)'].apply(lambda x : cat_pop(x) )
# df_pop.groupby('cat_pop').size()
df_pop = df_pop.groupby('cat_pop').sum().reset_index()
df_pop


cat_pop  População (2020)      cura     obito  \
0      0. até 5 mil         4183314.0   19622.0    9639.0   
1     1. 5 a 10 mil         8541879.0   33310.0   18033.0   
2    2. 10 a 20 mil        19024578.0   71444.0   38198.0   
3    3. 20 a 50 mil        33828245.0  144086.0   76014.0   
4   4. 50 a 200 mil        47006431.0  264867.0  134256.0   
5  5. 200 a 500 mil        31601488.0  203639.0  107329.0   
6  6. 500 mil a 1MM        21121066.0  145812.0   74965.0   
7          7. > 1MM        46400712.0  361401.0  182852.0   

   obito_outras_causas  casos_concluidos  letalidade    mortalidade  \
0                 76.0           29337.0  466.943073  293843.632301   
1                160.0           51503.0  488.676264  253182.962573   
2                364.0          110006.0  540.635052  266776.565385   
3                762.0          220862.0  447.826972  246592.612054   
4               1226.0          400349.0  200.045332  145266.527017   
5                620.0          311588.0   38.817143   35531.551398   
6                851.0          221628.0   11.857210   11267.218988   
7               1718.0          545971.0    6.093698    6536.707687   

   percent_rural  
0     553.493430  
1     487.228455  
2     526.801186  
3     351.188365  
4      88.953531  
5       4.578385  
6       0.682417  
7       0.134971

### Letalidade

In [25]:
#hide_input
#collapse_output

df = df_pop.groupby('cat_pop').sum().reset_index()
df['letalidade'] = df['obito'] / df['casos_concluidos']
df['mortalidade'] = 100000* (df['obito'] / df['População (2020)'])

chart = alt.Chart(df).mark_bar() 

x_col = 'cat_pop'
# sort_axis = 'x'
x_col_ed = x_col
# x_col_ed=alt.X(f'{x_col}:N', sort='y')
   
chart = chart.encode(
    x=x_col_ed,
    # color='mortalidade',
    color = 'População (2020)',
    y='letalidade',
    # y='mortalidade',
    # color='letalidade',
    tooltip=list(df_pop.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)

### Mortalidade

In [26]:
#hide_input
#collapse_output

df = df_pop.groupby('cat_pop').sum().reset_index()
df['letalidade'] = df['obito'] / df['casos_concluidos']
df['mortalidade'] = 100000* (df['obito'] / df['População (2020)'])

chart = alt.Chart(df).mark_bar() 

x_col = 'cat_pop'
# sort_axis = 'x'
x_col_ed = x_col
# x_col_ed=alt.X(f'{x_col}:N', sort='y')
   
chart = chart.encode(
    x=x_col_ed,
    # color='mortalidade',
    color = 'População (2020)',
    # y='letalidade',
    y='mortalidade',
    # color='letalidade',
    tooltip=list(df_pop.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)